---

# S03E03 : Concepts avancés - Closures

Cyril Desjouy

---


## Rappels sur les *namespaces* et les variables non locales

Si vous n'êtes pas à l'aise avec les ***fonctions imbriquées*** et les ***variables non locales***, il est fortement conseillé de revoir les notebooks de la saison 1 (**S01Exx**) concernant les *namespaces* avant d'aborder les ***closures***.

Pour rappel, une fonction imbriquée (appelé *nested function*) est une fonction dans une fonction. La particularité des fonctions imbriquées est qu'elles peuvent accéder aux variables du ***namespace*** de la fonction l'entourant appelé ***enclosed namespace***. Par exemple:

In [ ]:
def outer(msg):     # Enclosed namespace
    def inner():    # Local namespace
        print(msg)
    inner()

# Global namespace
outer('Python')

La fonction `inner` a ici accès **en lecture** à l'identifieur non local `msg`. Il n'est pas possible de le modifier à partir de `inner`:

In [ ]:
def outer(msg):     # Enclosed namespace
    def inner():    # Local namespace
        print(msg)
        msg = 'Hello'
        print(msg)
    inner()

# Global namespace
outer('Python')

Pour avoir accès en écriture à `msg`, il faut le déclarer comme `nonlocal` comme nous l'avons vu précédemment:

In [ ]:
def outer(msg):     # Enclosed namespace
    def inner():    # Local namespace
        nonlocal msg
        print(msg)
        msg = 'Hello'
        print(msg)
    inner()

# Global namespace
outer('Python')

## Le concept de *closure*

Une ***closure*** est une fonction à laquelle des données d'un ***enclosed scope*** sont attachées même si ces dernières ne sont plus présentes en mémoire. Ceci permet à la fonction d'être exécutée en dehors de l'endroit où elle a été définie.

<div class="alert alert-block alert-info">
Afin d'illustrer le concept de <b>closures</b>, modifions le tout premier exemple de ce notebook afin que la fonction <code>outer</code> retourne la fonction <code>inner</code> plutôt que de l'appeler:
</div>

In [ ]:
def outer(msg):     # Enclosed namespace
    def inner():    # Local namespace
        print(msg)
    return inner

# Global namespace
inside = outer('Python') 
del outer           # Removes outer from memory
inside()            # call inside

Surprenant non ?

La fonction `outer` est appelée avec l'argument d'entrée `'Python'`. Elle  retourne la fonction `inner` assignée à la variable `inside`. La fonction `outer` est alors appelée `factory function`. Elle permet en effet de créer des fonctions à chaque fois qu'elle est appelée. 

Lors de l'appel de `inside`, l'objet référencé par `msg` est affiché. Notons que ceci arrive même si l'exécution de `outer` est terminée et que l'objet `outer` à été supprimé de la mémoire (`del`). 

En fait, la fonction `inside` se souvient de l'état de son environnement lorsqu'elle est appelée. C'est le mécanisme selon lequel des données (`'Python'`) sont attachées à une fonction (`inside`) qu'on appelle ***closure***. Sans l'existence de ce mécanisme, les fonctions imbriquées présenteraient un intérêt relativement limité! 


## Recette de cuisine

Pour produire une ***closure***, il faut :

* qu'une fonction imbriquée **fasse référence** à une valeur de la fonction l'entourant.
* que la fonction entourante **retourne** impérativement la fonction imbriquée.

## Quand les utiliser ?

Les ***closures*** peuvent permettre:

* d'éviter les variables globales,
* de cacher des données,
* d'implémenter des alternatives élégantes aux classes lorsqu'elles ont peu de méthodes,
* de développer des ***decorators*** que vous verrons dans l'épisode **S03E04** suivant.

## Accéder aux données

Les objets de type `function` héritent de l'attribut `__closure__`. Cet attribut est généralement `None` sauf si la fonction est une ***closure***. Dans ce cas `__closure__` est un tuple dont chaque élément hérite de l'attribut `cell_contents` contenant les données enfermées:

```python
>> inside = outer('Python') 
>> inside.__closure__[0].cell_contents   # returns 'Python'
```

## Closures et mutabilité

Il est important de préciser que les références contenues dans la ***closure*** sont juste des références, et pas des copies des objets. Ceci n'a pas d'importance lorsque les identifieurs contenues dans la ***closure*** référencent des objets immuables, mais il faut être vigilant lorsqu'il s'agit d'objets mutables.

<div class="alert alert-block alert-info">
Testez le bloc de code suivant en essayant de bien comprendre ce qui se passe:
</div>

In [ ]:
def outer(msg):     # Enclosed namespace
    def inner():    # Local namespace
        print(msg)
    return inner

# Global namespace
lst = [1, 2]
inside = outer(lst) 
inside()            
lst.append(3)       # In-place modification of lst
inside()
lst = [1]           # New object lst
inside()

## Application: Beers please!

Considérez la classe suivante:
```python
class Beer:
    
    def __init__(self, which):
        self.which = which
    
    def serve(self, n):
        return 'Serve {} pint(s) of {}'.format(n, self.which)
    
guinness = Beer('Guinness')
guinness.serve(6)             # returns 'Serve 6 pint(s) of Guinness'


```
<div class="alert alert-block alert-info">
Utilisez une <b><i>closure</i></b> pour arriver to même résultat.
</div>
